# 3D Scans
Voor het trainen op 3D scans zijn een aantal aanpassingen nodig. In dit notebook staan deze aanpassingen beschreven.

In [1]:
import tqdm
import glob
import joblib
import numpy as np
import tensorflow as tf
import keras.layers as layers
from support_functions import *
from keras import Sequential, Model
from keras.callbacks import Callback
import sklearn.model_selection as model_selection

## 3D scans inzien
Als eerste is het handig om een 3D scan in te kunnen zien. Hiervoor is de functie display_3d_scan gescreven, die te vinden is in support_functions.py.

In [9]:
display_3d_scan(read_dicom_slices('scans/CAC-Scans-Anonymous/1'))

Met behulp van de corrup_3d_image functie is het ook mogelijk om deze scans te corrumperen in drie dimensies.

In [10]:
NUMBER_OF_SWITCHES = 16
PATCH_SIZE = 32
display_3d_scan(corrupt_3d_image(read_dicom_slices('scans/CAC-Scans-Anonymous/1'), NUMBER_OF_SWITCHES, PATCH_SIZE))

## Data generator
In deze data generator worden per batch de scans uitgelezen, geschaald, dezelfde shape gemaakt en gecorrumpeerd. Deze data generator kan als input worden gebruikt bij het trainen van het model en zorgt ervoor dat de gehele dataset niet ingeladen hoeft te worden.

In [2]:
class data_generator(tf.keras.utils.Sequence):
    def __init__(self, scans, batch_size, number_of_switches, patch_size) :
        self.scans = scans
        self.batch_size = batch_size
        self.number_of_switches = number_of_switches
        self.patch_size = patch_size
    
    
    def __len__(self) :
        return (np.ceil(len(self.scans) / float(self.batch_size))).astype(int)
  
  
    def __getitem__(self, idx) :
        
        batch_y = self.scans[idx * self.batch_size : (idx+1) * self.batch_size]
        
        arr = np.empty((0, 40, 512, 512), int)
        
        # pak de middelste 40 slices uit een scan
        for path in batch_y:
            scan = read_dicom_slices(path)
        
            if scan.shape[0] > 40:
                offset = (scan.shape[0] - 40) // 2
                scan = scan[offset:-offset]
        
            if scan.shape[0] is 41:
                scan = scan[:40]
        
            arr = np.concatenate((arr, [scan]), axis=0)
            
        # min max scalen
        batch_y = np.float32((arr - -91) / (4095 - -91))
        
        # corrupten
        batch_X = np.array([corrupt_3d_image(scan, self.number_of_switches, self.patch_size) for scan in batch_y])
    
        # reshape
        batch_X = np.resize(batch_X, (batch_X.shape[0], batch_X.shape[1], batch_X.shape[2], batch_X.shape[3], 1))
        batch_y = np.resize(batch_y, (batch_y.shape[0], batch_y.shape[1], batch_y.shape[2], batch_y.shape[3], 1))
    
    
        return batch_X, batch_y

Als input heeft de data generator een lijst met scans nodig. Hieronder wordt de lijst van scans gefilterd en willekeurig gesorteerd.

In [3]:
scans = glob('scans/CAC-Scans-Anonymous/*')
scans.remove('scans/CAC-Scans-Anonymous/288')
scans.remove('scans/CAC-Scans-Anonymous/289')
scans.remove('scans/CAC-Scans-Anonymous/290')
len(scans)

502

In [4]:
np.random.shuffle(scans)
train_scans = scans[: int(len(scans) * 0.8)]
test_scans = scans[int(len(scans) * 0.8) :]
print(len(train_scans))
print(len(test_scans))

401
101


Vervolgens kan er voor de train en test lijst een data generator aangemaakt worden met de juiste parameters.

In [5]:
batch_size = 2
no_switches = 16
patch_size = 32

train_batch_gen = data_generator(train_scans, batch_size, no_switches, patch_size)
test_batch_gen = data_generator(test_scans, batch_size, no_switches, patch_size)

## Modelling
Hieronder wordt een model gedefinieerd wat de 3D scans als input heeft.

In [6]:
limit_gpu_memory(6 * 1024)
strategy = tf.distribute.MirroredStrategy()

INFO:tensorflow:Using MirroredStrategy with devices ('/job:localhost/replica:0/task:0/device:GPU:0', '/job:localhost/replica:0/task:0/device:GPU:1')


In [7]:
analyzer_input_shape = (40, 256, 256, 1)
reconstructor_input_shape = (10, 64, 64, 256)

In [8]:
with strategy.scope():
    analyzer = Sequential(
        [
            layers.Conv3D(128, kernel_size=3, input_shape=analyzer_input_shape, padding='same', activation='relu'),
            layers.Conv3D(128, kernel_size=3, padding='same', activation='relu'),
            layers.Conv3D(128, kernel_size=3, padding='same', activation='relu'),
            layers.MaxPooling3D(pool_size=(2, 2, 2)),

            layers.Conv3D(256, kernel_size=3, padding='same', activation='relu'),
            layers.Conv3D(256, kernel_size=3, padding='same', activation='relu'),
            layers.Conv3D(256, kernel_size=3, padding='same', activation='relu'),
            layers.MaxPooling3D(pool_size=(2, 2, 2)),
        ],
        name="analyzer",
    )
    analyzer.summary()

Model: "analyzer"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv3d (Conv3D)              (None, 40, 256, 256, 128) 3584      
_________________________________________________________________
conv3d_1 (Conv3D)            (None, 40, 256, 256, 128) 442496    
_________________________________________________________________
conv3d_2 (Conv3D)            (None, 40, 256, 256, 128) 442496    
_________________________________________________________________
max_pooling3d (MaxPooling3D) (None, 20, 128, 128, 128) 0         
_________________________________________________________________
conv3d_3 (Conv3D)            (None, 20, 128, 128, 256) 884992    
_________________________________________________________________
conv3d_4 (Conv3D)            (None, 20, 128, 128, 256) 1769728   
_________________________________________________________________
conv3d_5 (Conv3D)            (None, 20, 128, 128, 256) 176

In [9]:
with strategy.scope():
    reconstructor = Sequential(
        [
            layers.Conv3DTranspose(256, kernel_size=3, strides=(2, 2, 2), padding='same', input_shape=reconstructor_input_shape, activation='relu'),
            layers.Conv3DTranspose(128, kernel_size=3, strides=(2, 2, 2), padding='same', activation='relu'),
            layers.Conv3D(1, kernel_size=3, padding='same'),
        ],
        name="reconstructor",
    )
    reconstructor.summary()

Model: "reconstructor"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv3d_transpose (Conv3DTran (None, 20, 128, 128, 256) 1769728   
_________________________________________________________________
conv3d_transpose_1 (Conv3DTr (None, 40, 256, 256, 128) 884864    
_________________________________________________________________
conv3d_6 (Conv3D)            (None, 40, 256, 256, 1)   3457      
Total params: 2,658,049
Trainable params: 2,658,049
Non-trainable params: 0
_________________________________________________________________


In [10]:
with strategy.scope():
    out_analyzer = analyzer.output
    out_final = reconstructor(out_analyzer)
    model = Model(analyzer.input, out_final)
    
    model.compile(optimizer='adam', loss='mse')

INFO:tensorflow:Reduce to /job:localhost/replica:0/task:0/device:CPU:0 then broadcast to ('/job:localhost/replica:0/task:0/device:CPU:0',).
INFO:tensorflow:Reduce to /job:localhost/replica:0/task:0/device:CPU:0 then broadcast to ('/job:localhost/replica:0/task:0/device:CPU:0',).
INFO:tensorflow:Reduce to /job:localhost/replica:0/task:0/device:CPU:0 then broadcast to ('/job:localhost/replica:0/task:0/device:CPU:0',).
INFO:tensorflow:Reduce to /job:localhost/replica:0/task:0/device:CPU:0 then broadcast to ('/job:localhost/replica:0/task:0/device:CPU:0',).


Op dit moment gebruiken we een andere callback dan bij het 2D model, aangezien we niet goed konden testen of de 3D triplets zouden werken. Wel staat deze functie, display_3d_triplets, in het bestand support_functions.py.

In [11]:
checkpoint_filepath = 'models/model_3d_scans/checkpoint'

model_checkpoint_callback = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_filepath,
    save_best_only=True,
    monitor='loss',
    mode='min',
    save_weights_only=False,
    verbose=0
)

In [ ]:
with strategy.scope():
    history = model.fit(train_batch_gen,
                        steps_per_epoch = int(len(train_scans) // batch_size),
                        epochs = 10,
                        validation_data = test_batch_gen,
                        validation_steps = int(len(test_scans) // batch_size),
                        use_multiprocessing=True,
                        callbacks=[model_checkpoint_callback])

Epoch 1/10
INFO:tensorflow:batch_all_reduce: 18 all-reduces with algorithm = nccl, num_packs = 1
INFO:tensorflow:Reduce to /job:localhost/replica:0/task:0/device:CPU:0 then broadcast to ('/job:localhost/replica:0/task:0/device:CPU:0',).
INFO:tensorflow:Reduce to /job:localhost/replica:0/task:0/device:CPU:0 then broadcast to ('/job:localhost/replica:0/task:0/device:CPU:0',).
INFO:tensorflow:batch_all_reduce: 18 all-reduces with algorithm = nccl, num_packs = 1
INFO:tensorflow:Reduce to /job:localhost/replica:0/task:0/device:CPU:0 then broadcast to ('/job:localhost/replica:0/task:0/device:CPU:0',).
INFO:tensorflow:Reduce to /job:localhost/replica:0/task:0/device:CPU:0 then broadcast to ('/job:localhost/replica:0/task:0/device:CPU:0',).


Tot zover hebben we de 3D modellen werkend gekregen. Bij het trainen blijkt dat er niet genoeg VRAM is om te kunnen trainen.